# Business Data Challenge - Team 1

In [1]:
import pandas as pd
import numpy as np
import os
import s3fs
import re

Configuration de l'accès aux données

In [2]:
# Create filesystem object
S3_ENDPOINT_URL = "https://" + os.environ["AWS_S3_ENDPOINT"]
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url': S3_ENDPOINT_URL})

# Exemple sur Company 1

## Chargement données

In [3]:
BUCKET = "bdc2324-data/1"
liste_database = fs.ls(BUCKET)

In [5]:
liste_database_select = ['suppliers', 'ticket', 'purchase', 'consumption', 'type_ofs']

# Filtrer la liste pour les éléments contenant au moins un élément de la liste à tester
liste_database_filtered = [element for element in liste_database if any(element_part in element for element_part in liste_database_select)]

# Afficher le résultat
print(liste_database_filtered)

['bdc2324-data/1/1purchases.csv', 'bdc2324-data/1/1suppliers.csv', 'bdc2324-data/1/1tickets.csv', 'bdc2324-data/1/1type_ofs.csv']


In [6]:
# loop to create dataframes from liste
files_path = liste_database

client_number = files_path[0].split("/")[1]
df_prefix = "df" + str(client_number) + "_"

for i in range(len(files_path)) :
    current_path = files_path[i]
    with fs.open(current_path, mode="rb") as file_in:
        df = pd.read_csv(file_in)
        # the pattern of the name is df1xxx
        nom_dataframe = df_prefix + re.search(r'\/(\d+)\/(\d+)([a-zA-Z_]+)\.csv$', current_path).group(3)
        globals()[nom_dataframe] = df

/tmp/ipykernel_445/4081512283.py:10: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_in)


## customersplus.csv

In [22]:
a = pd.DataFrame(df1_customersplus.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 151866 entries, 0 to 151865
Data columns (total 29 columns):
 #   Column                  Non-Null Count   Dtype  
---  ------                  --------------   -----  
 0   id                      151866 non-null  int64  
 1   birthdate               5437 non-null    object 
 2   street_id               151866 non-null  int64  
 3   civility                0 non-null       float64
 4   is_partner              151866 non-null  bool   
 5   deleted_at              0 non-null       float64
 6   gender                  151866 non-null  int64  
 7   is_email_true           151866 non-null  bool   
 8   opt_in                  151866 non-null  bool   
 9   structure_id            18114 non-null   float64
 10  note                    906 non-null     object 
 11  profession              6206 non-null    object 
 12  language                1092 non-null    object 
 13  mcp_contact_id          98901 non-null   float64
 14  last_buying_date    

In [31]:
def info_colonnes_dataframe(df):
    # Créer une liste pour stocker les informations sur chaque colonne
    infos_colonnes = []

    # Parcourir les colonnes du DataFrame
    for nom_colonne, serie in df.items():  # Utiliser items() au lieu de iteritems()
        # Calculer le taux de valeurs manquantes
        taux_na = serie.isna().mean() * 100

        # Ajouter les informations à la liste
        infos_colonnes.append({
            'Nom_colonne': nom_colonne,
            'Type_colonne': str(serie.dtype),
            'Taux_NA': taux_na
        })

    # Créer une nouvelle DataFrame à partir de la liste d'informations
    df_infos_colonnes = pd.DataFrame(infos_colonnes)

    return df_infos_colonnes

In [35]:
def cleaning_date(df, column_name):
    """
    Nettoie la colonne spécifiée du DataFrame en convertissant les valeurs en datetime avec le format ISO8601.

    Parameters:
    - df: DataFrame
        Le DataFrame contenant la colonne à nettoyer.
    - column_name: str
        Le nom de la colonne à nettoyer.

    Returns:
    - DataFrame
        Le DataFrame modifié avec la colonne nettoyée.
    """
    df[column_name] = pd.to_datetime(df[column_name], utc = True, format = 'ISO8601')
    return df

In [32]:
a = info_colonnes_dataframe(df1_customersplus)

In [33]:
a

Nom_colonne Type_colonne     Taux_NA
0                       id        int64    0.000000
1                 lastname       object   43.461341
2                firstname       object   44.995588
3                birthdate       object   96.419870
4                    email       object    8.622075
5                street_id        int64    0.000000
6               created_at       object    0.000000
7               updated_at       object    0.000000
8                 civility      float64  100.000000
9               is_partner         bool    0.000000
10                   extra      float64  100.000000
11              deleted_at      float64  100.000000
12               reference      float64  100.000000
13                  gender        int64    0.000000
14           is_email_true         bool    0.000000
15             extra_field      float64  100.000000
16              identifier       object    0.000000
17                  opt_in         bool    0.000000
18            structure_id      float64   88.072380
19                    note       object   99.403421
20              profession       object   95.913503
21                language       object   99.280945
22          mcp_contact_id      float64   34.876141
23             need_reload         bool    0.000000
24        last_buying_date       object   51.653431
25               max_price      float64   51.653431
26              ticket_sum        int64    0.000000
27           average_price      float64    8.639195
28                fidelity        int64    0.000000
29  average_purchase_delay      float64   51.653431
30    average_price_basket      float64   51.653431
31   average_ticket_basket      float64   51.653431
32             total_price      float64   43.014236
33      preferred_category      float64  100.000000
34      preferred_supplier      float64  100.000000
35       preferred_formula      float64  100.000000
36          purchase_count        int64    0.000000
37       first_buying_date       object   51.653431
38      last_visiting_date      float64  100.000000
39                 zipcode       object   71.176564
40                 country       object    5.459418
41                     age      float64   96.419870
42               tenant_id        int64    0.000000

In [16]:
a = pd.DataFrame(df1_customersplus.isna().sum()/len(df1_customersplus)*100)

In [40]:
# Selection des variables
df1_customersplus_clean = df1_customersplus.copy()

cleaning_date(df1_customersplus_clean, 'first_buying_date')
cleaning_date(df1_customersplus_clean, 'last_visiting_date')

df1_customersplus_clean.drop(['lastname', 'firstname', 'email', 'civility', 'note', 'created_at', 'updated_at', 'deleted_at', 'extra', 'reference', 'extra_field', 'identifier', 'need_reload', 'preferred_category', 'preferred_supplier', 'preferred_formula', 'zipcode', 'last_visiting_date'], axis = 1, inplace=True)
df1_customersplus_clean.rename(columns = {'id' : 'customer_id'}, inplace = True)



customer_id birthdate  street_id  is_partner  gender  is_email_true  \
0        12751       NaN          2       False       1           True   
1        12825       NaN          2       False       2           True   
2        11261       NaN          2       False       1           True   
3        13071       NaN          2       False       2           True   
4       653061       NaN         10       False       2           True   

   opt_in  structure_id note profession  ... fidelity  average_purchase_delay  \
0    True           NaN  NaN        NaN  ...        0                     NaN   
1    True           NaN  NaN        NaN  ...        0                     NaN   
2    True           NaN  NaN        NaN  ...        0                     NaN   
3    True           NaN  NaN        NaN  ...        0                     NaN   
4   False           NaN  NaN        NaN  ...        0                     NaN   

  average_price_basket  average_ticket_basket  total_price  purchase_count  \
0                  NaN                    NaN          NaN               0   
1                  NaN                    NaN          NaN               0   
2                  NaN                    NaN          NaN               0   
3                  NaN                    NaN          NaN               0   
4                  NaN                    NaN          NaN               0   

   first_buying_date  country  age  tenant_id  
0                NaT       fr  NaN       1311  
1                NaT       fr  NaN       1311  
2                NaT       fr  NaN       1311  
3                NaT       fr  NaN       1311  
4                NaT      NaN  NaN       1311  

[5 rows x 26 columns]

## tickets.csv

In [6]:
df1_tickets

id          number                        created_at  \
0        13070859  13593002661288  2021-12-28 20:47:10.320641+01:00   
1        13070860  13593002661399  2021-12-28 20:47:10.321037+01:00   
2        13070861  13593002661419  2021-12-28 20:47:10.321629+01:00   
3        13070862  13593002661508  2021-12-28 20:47:10.322029+01:00   
4        13070863  13593002661689  2021-12-28 20:47:10.322449+01:00   
...           ...             ...                               ...   
1826667  20662815  13593016154390  2023-11-09 07:51:34.935983+01:00   
1826668  20662816  13593016154501  2023-11-09 07:51:34.937038+01:00   
1826669  20662817  13593016154680  2023-11-09 07:51:34.938224+01:00   
1826670  20662818  13593016154899  2023-11-09 07:51:34.939328+01:00   
1826671  20662819  13593016154988  2023-11-09 07:51:34.940680+01:00   

                               updated_at  purchase_id  product_id  \
0        2022-02-14 18:46:53.614229+01:00      5107462      225251   
1        2022-02-14 18:46:53.614761+01:00      5107462      224914   
2        2022-02-14 18:46:53.615521+01:00      5107462      224914   
3        2022-02-14 18:46:53.616000+01:00      5107462      224914   
4        2022-02-14 18:46:53.616447+01:00      5107462      224914   
...                                   ...          ...         ...   
1826667  2023-11-09 07:51:34.935983+01:00      8007697      405689   
1826668  2023-11-09 07:51:34.937038+01:00      8007698      403658   
1826669  2023-11-09 07:51:34.938224+01:00      8007698      403658   
1826670  2023-11-09 07:51:34.939328+01:00      8007699      403658   
1826671  2023-11-09 07:51:34.940680+01:00      8007699      403658   

         is_from_subscription  type_of  supplier_id  barcode  \
0                       False        1            3      NaN   
1                       False        1            3      NaN   
2                       False        1            3      NaN   
3                       False        1            3      NaN   
4                       False        1            3      NaN   
...                       ...      ...          ...      ...   
1826667                 False        1            3      NaN   
1826668                 False        1            3      NaN   
1826669                 False        1            3      NaN   
1826670                 False        1            3      NaN   
1826671                 False        1            3      NaN   

                               identifier  
0        b6ad7fc36f33b5e05f58c7fca06688a6  
1        b0903af480266f27802fe5c38c277c9e  
2        64ca12b7e26a65b90335c0702ea0faba  
3        5ac2f8150aa9f3a6b1599df08cc2f0c7  
4        dfe30081bae020d12094279926136b9c  
...                                   ...  
1826667  dba9aa428f843b79ae69dfacfe8fc579  
1826668  93f1fcfc6ba4fa68f92eb4b4a619fcf0  
1826669  c8bbbd25df2c158767ceef42c3237f23  
1826670  738f0a8b5088b5056bc3b32eff2dca1f  
1826671  4c5a6195434377380b4e6ae63b2e9cf6  

[1826672 rows x 11 columns]

In [7]:
df1_tickets.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1826672 entries, 0 to 1826671
Data columns (total 11 columns):
 #   Column                Dtype  
---  ------                -----  
 0   id                    int64  
 1   number                object 
 2   created_at            object 
 3   updated_at            object 
 4   purchase_id           int64  
 5   product_id            int64  
 6   is_from_subscription  bool   
 7   type_of               int64  
 8   supplier_id           int64  
 9   barcode               float64
 10  identifier            object 
dtypes: bool(1), float64(1), int64(5), object(4)
memory usage: 141.1+ MB


In [8]:
df1_tickets.isna().sum()/len(df1_tickets)*100

id                        0.0
number                    0.0
created_at                0.0
updated_at                0.0
purchase_id               0.0
product_id                0.0
is_from_subscription      0.0
type_of                   0.0
supplier_id               0.0
barcode                 100.0
identifier                0.0
dtype: float64

In [9]:
# Selection des variables
df1_tickets_clean = df1_tickets.drop(['lastname', 'firstname', 'email', 'created_at', 'updated_at', 'extra', 'reference', 'extra_field', 'identifier', 'need_reload', 'preferred_category', 'preferred_supplier', 'preferred_formula', 'zipcode'], axis = 1, inplace=True)
df1_tickets_clean.rename(columns = {'id' : 'customer_id'}, inplace = True)

/tmp/ipykernel_619/232847087.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1_tickets_clean.rename(columns = {'id' : 'ticket_id'}, inplace = True)


## suppliers.csv

In [10]:
df1_suppliers

id               name  manually_added  label  itr  \
0  1617  j4 administration           False    NaN  NaN   
1     8         non défini           False    NaN  NaN   
2     4                vad           False    NaN  NaN   
3     1    fort saint jean           False    NaN  NaN   
4     2                 j4           False    NaN  NaN   
5     5          revendeur           False    NaN  NaN   
6     3     vente en ligne           False    NaN  NaN   
7     6                ccr           False    NaN  NaN   
8     7                dab           False    NaN  NaN   

                         updated_at                        created_at  \
0  2021-07-29 09:21:37.325772+02:00  2021-07-29 09:21:37.325772+02:00   
1  2020-09-03 13:16:35.329062+02:00  2020-09-03 13:16:35.329062+02:00   
2  2020-09-03 13:11:23.896992+02:00  2020-09-03 13:11:23.896992+02:00   
3  2020-09-03 13:11:23.833073+02:00  2020-09-03 13:11:23.833073+02:00   
4  2020-09-03 13:11:23.888993+02:00  2020-09-03 13:11:23.888993+02:00   
5  2020-09-03 13:11:23.900987+02:00  2020-09-03 13:11:23.900987+02:00   
6  2020-09-03 13:11:23.893097+02:00  2020-09-03 13:11:23.893097+02:00   
7  2020-09-03 13:11:23.904974+02:00  2020-09-03 13:11:23.904974+02:00   
8  2020-09-03 13:11:23.908970+02:00  2020-09-03 13:11:23.908970+02:00   

   commission                        identifier  
0         NaN  5958b2a060ac3e31678b438892a1bd2e  
1         NaN  52ff3466787b4d538407372e5f7afe0f  
2         NaN  1225483c97b36018cab2bea14ab78ea6  
3         NaN  001b9b4a524fe407150b8235b304d4ec  
4         NaN  6a0cf6edf20060344b465706b61719aa  
5         NaN  931239d4acb6214d7e5c98edecfb4916  
6         NaN  bde8f2ccff510df8572d3214d86b837d  
7         NaN  b48ec279411f7dbbb68393c61a9724d9  
8         NaN  11c6d471fa4e354e62e684d293694202

In [11]:
df1_suppliers.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9 entries, 0 to 8
Data columns (total 9 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   id              9 non-null      int64  
 1   name            9 non-null      object 
 2   manually_added  9 non-null      bool   
 3   label           0 non-null      float64
 4   itr             0 non-null      float64
 5   updated_at      9 non-null      object 
 6   created_at      9 non-null      object 
 7   commission      0 non-null      float64
 8   identifier      9 non-null      object 
dtypes: bool(1), float64(3), int64(1), object(4)
memory usage: 713.0+ bytes


In [12]:
df1_suppliers.isna().sum()/len(df1_suppliers)*100

id                  0.0
name                0.0
manually_added      0.0
label             100.0
itr               100.0
updated_at          0.0
created_at          0.0
commission        100.0
identifier          0.0
dtype: float64

In [13]:
# Selection des variables
df1_suppliers_clean = df1_suppliers[['id', 'name']]
df1_suppliers_clean.rename(columns = {'name' : 'supplier_name'}, inplace = True)

/tmp/ipykernel_619/302783287.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1_suppliers_clean.rename(columns = {'name' : 'supplier_name'}, inplace = True)


In [14]:
df1_suppliers_clean

id      supplier_name
0  1617  j4 administration
1     8         non défini
2     4                vad
3     1    fort saint jean
4     2                 j4
5     5          revendeur
6     3     vente en ligne
7     6                ccr
8     7                dab

## type_ofs.csv

In [15]:
df1_type_ofs

id               name         children                        created_at  \
0    1            Atelier  pricing_formula  2021-01-05 11:55:51.188106+01:00   
1    2   Billet en nombre  pricing_formula  2021-01-11 12:13:19.286301+01:00   
2    3             Groupe  pricing_formula  2021-01-11 12:19:22.842917+01:00   
3    4          Revendeur  pricing_formula  2021-01-12 12:34:20.481236+01:00   
4    5    Cinéma scolaire  pricing_formula  2021-01-25 19:16:05.141719+01:00   
5    6      Musée famille  pricing_formula  2021-01-25 19:23:06.692627+01:00   
6    7  Spectacle famille  pricing_formula  2021-01-25 19:28:21.390016+01:00   
7    8        Masterclass  pricing_formula  2021-01-25 19:31:05.076904+01:00   
8    9          Spectacle  pricing_formula  2021-01-25 19:38:41.260535+01:00   
9   10             Cinema  pricing_formula  2021-02-05 11:12:31.932576+01:00   
10  11              Musee  pricing_formula  2021-02-05 11:52:05.468207+01:00   
11  12       Tarifs plein         category  2023-03-13 11:31:50.528331+01:00   

                          updated_at                        identifier  
0   2021-01-05 11:55:51.188106+01:00  623ec4067827558b28972cf39fe81ee7  
1   2021-01-11 12:13:19.286301+01:00  a53d313a97296ee37caa066dbfe7a45c  
2   2021-01-11 12:19:22.842917+01:00  1ab143efc3b85acbbc752fe8eb2b0b86  
3   2021-01-12 12:34:20.481236+01:00  8b332723366a07e1eef5f1c92f9ae067  
4   2021-01-25 19:16:05.141719+01:00  a12e62cb4c4f47e7406bd8fbff2bfe30  
5   2021-01-25 19:23:06.692627+01:00  1ec6c19283111ccb3ed67f52d414470e  
6   2021-01-25 19:28:21.390016+01:00  05e2104f1b74ced229c06847d6e91938  
7   2021-01-25 19:31:05.076904+01:00  9cc946edfb25e11b4282f58db16e6ae9  
8   2021-01-25 19:38:41.260535+01:00  d88321c347f0e0ab101184cdf25c94bf  
9   2021-02-05 11:12:31.932576+01:00  0870fef2bfcd5b30a12e4f5c7f4aaba7  
10  2021-02-05 11:52:05.468207+01:00  8ba8934454cc62c7cdb3eb6e1b39df0c  
11  2023-03-13 11:31:50.528331+01:00  a6969df76efc15d157be48e87a7bcf9a

In [16]:
df1_type_ofs.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12 entries, 0 to 11
Data columns (total 6 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   id          12 non-null     int64 
 1   name        12 non-null     object
 2   children    12 non-null     object
 3   created_at  12 non-null     object
 4   updated_at  12 non-null     object
 5   identifier  12 non-null     object
dtypes: int64(1), object(5)
memory usage: 704.0+ bytes


In [17]:
# Selection des variables
df1_type_ofs_clean = df1_type_ofs[['id', 'name', 'children']]
df1_type_ofs_clean.rename(columns = {'name' : 'type_of_ticket_name'}, inplace = True)

/tmp/ipykernel_619/81842251.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1_type_ofs_clean.rename(columns = {'name' : 'type_of_ticket_name'}, inplace = True)


## purchases.csv

In [18]:
df1_purchases

id              purchase_date  customer_id  \
0       5145662  2019-07-17 11:17:53+02:00         6632   
1       4941642  2018-10-31 11:59:00+01:00            1   
2       5088860  2018-10-31 12:45:12+01:00            1   
3       5088862  2018-10-31 13:07:12+01:00            1   
4       5088863  2018-10-31 13:08:50+01:00            1   
...         ...                        ...          ...   
742245  8007695  2023-11-08 17:51:19+01:00      1256133   
742246  8007696  2023-11-08 18:17:51+01:00      1256134   
742247  8007697  2023-11-08 18:23:54+01:00      1256135   
742248  8007698  2023-11-08 19:32:18+01:00      1256136   
742249  8007699  2023-11-08 20:30:28+01:00      1256137   

                              created_at                        updated_at  \
0       2021-12-28 20:48:51.569237+01:00  2021-12-28 20:48:51.569237+01:00   
1       2021-12-28 20:31:48.196681+01:00  2022-03-03 17:52:21.958861+01:00   
2       2021-12-28 20:46:34.703542+01:00  2021-12-28 20:46:34.703542+01:00   
3       2021-12-28 20:46:34.704773+01:00  2021-12-28 20:46:34.704773+01:00   
4       2021-12-28 20:46:34.705453+01:00  2021-12-28 20:46:34.705453+01:00   
...                                  ...                               ...   
742245  2023-11-09 07:51:33.920187+01:00  2023-11-09 07:51:33.920187+01:00   
742246  2023-11-09 07:51:33.921967+01:00  2023-11-09 07:51:33.921967+01:00   
742247  2023-11-09 07:51:33.923034+01:00  2023-11-09 07:51:33.923034+01:00   
742248  2023-11-09 07:51:33.924135+01:00  2023-11-09 07:51:33.924135+01:00   
742249  2023-11-09 07:51:33.925382+01:00  2023-11-09 07:51:33.925382+01:00   

                                  number                        identifier  
0       fa80c83b29a268b45728c910a8afcf79  82877c41df26f832eb823a83acd1a172  
1       597b6c06adfe6acc539b29b657b80da0  e7102ebe65526c427245533ebabe66e5  
2       4a7f6baaf9be6a99e3fead7f7e981fa8  af75c4ae53d1b6957875538355b162e1  
3       1d83dfad44b73070d1c6d5875d0edd2d  4b2fe34659b177209b07270ae1043b40  
4       7bfe2bc9c1670c973d0960e3fd408cf8  b115f04a99b94df9e4a32185844f0998  
...                                  ...                               ...  
742245  99ad774dedbad43feb73514765d2f0ba  d68558180b4bf2e8a945724843655775  
742246  c1511614c511c5f95980172690179102  f5102d910a7731091f239ad7b0df35b4  
742247  33b64b39cc53428b4f17d65ff5b93104  e2b917626be60cc2c3207cc037fe69e4  
742248  9ae0b129e704b3d9c093ce9c7c4e5039  5bfa23236c31f8562c3a0233c1b53b31  
742249  d31ced089c2b1f90479257a4686f9306  d86b1e0de3ff01eaf04fbcd031ac5fef  

[742250 rows x 7 columns]

In [19]:
df1_purchases.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 742250 entries, 0 to 742249
Data columns (total 7 columns):
 #   Column         Non-Null Count   Dtype 
---  ------         --------------   ----- 
 0   id             742250 non-null  int64 
 1   purchase_date  742250 non-null  object
 2   customer_id    742250 non-null  int64 
 3   created_at     742250 non-null  object
 4   updated_at     742250 non-null  object
 5   number         742250 non-null  object
 6   identifier     742250 non-null  object
dtypes: int64(2), object(5)
memory usage: 39.6+ MB


In [20]:
# Nettoyage purchase_date
df1_purchases['purchase_date'] = pd.to_datetime(df1_purchases['purchase_date'], utc = True)
df1_purchases['purchase_date'] = pd.to_datetime(df1_purchases['purchase_date'], format = 'ISO8601')

In [21]:
df1_purchases.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 742250 entries, 0 to 742249
Data columns (total 7 columns):
 #   Column         Non-Null Count   Dtype              
---  ------         --------------   -----              
 0   id             742250 non-null  int64              
 1   purchase_date  742250 non-null  datetime64[ns, UTC]
 2   customer_id    742250 non-null  int64              
 3   created_at     742250 non-null  object             
 4   updated_at     742250 non-null  object             
 5   number         742250 non-null  object             
 6   identifier     742250 non-null  object             
dtypes: datetime64[ns, UTC](1), int64(2), object(4)
memory usage: 39.6+ MB


In [22]:
# Selection des variables
df1_purchases_clean = df1_purchases[['id', 'purchase_date', 'customer_id']]

## Fusion de l'ensemble des données billétiques

In [23]:
# Fusion avec fournisseurs
df1_ticket_information = pd.merge(df1_tickets_clean, df1_suppliers_clean, left_on = 'supplier_id', right_on = 'id', how = 'inner')
df1_ticket_information.drop(['supplier_id', 'id'], axis = 1, inplace=True)

# Fusion avec type de tickets
df1_ticket_information = pd.merge(df1_ticket_information, df1_type_ofs_clean, left_on = 'type_of', right_on = 'id', how = 'inner')
df1_ticket_information.drop(['type_of', 'id'], axis = 1, inplace=True)

# Fusion avec achats
df1_ticket_information = pd.merge(df1_ticket_information, df1_purchases_clean, left_on = 'purchase_id', right_on = 'id', how = 'inner')
df1_ticket_information.drop(['purchase_id', 'id'], axis = 1, inplace=True)

In [24]:
df1_ticket_information

ticket_id  product_id  is_from_subscription   supplier_name  \
0         13070859      225251                 False  vente en ligne   
1         13070860      224914                 False  vente en ligne   
2         13070861      224914                 False  vente en ligne   
3         13070862      224914                 False  vente en ligne   
4         13070863      224914                 False  vente en ligne   
...            ...         ...                   ...             ...   
1826667   20662815      405689                 False  vente en ligne   
1826668   20662816      403658                 False  vente en ligne   
1826669   20662817      403658                 False  vente en ligne   
1826670   20662818      403658                 False  vente en ligne   
1826671   20662819      403658                 False  vente en ligne   

        type_of_ticket_name         children             purchase_date  \
0                   Atelier  pricing_formula 2018-12-28 14:47:50+00:00   
1                   Atelier  pricing_formula 2018-12-28 14:47:50+00:00   
2                   Atelier  pricing_formula 2018-12-28 14:47:50+00:00   
3                   Atelier  pricing_formula 2018-12-28 14:47:50+00:00   
4                   Atelier  pricing_formula 2018-12-28 14:47:50+00:00   
...                     ...              ...                       ...   
1826667             Atelier  pricing_formula 2023-11-08 17:23:54+00:00   
1826668             Atelier  pricing_formula 2023-11-08 18:32:18+00:00   
1826669             Atelier  pricing_formula 2023-11-08 18:32:18+00:00   
1826670             Atelier  pricing_formula 2023-11-08 19:30:28+00:00   
1826671             Atelier  pricing_formula 2023-11-08 19:30:28+00:00   

         customer_id  
0              48187  
1              48187  
2              48187  
3              48187  
4              48187  
...              ...  
1826667      1256135  
1826668      1256136  
1826669      1256136  
1826670      1256137  
1826671      1256137  

[1826672 rows x 8 columns]

# Utilisation de fonctions

In [51]:
# Créer un DataFrame exemple
df_not_clean = df1_campaign_stats[['opened_at']].head(20)

# Appliquer la fonction pour nettoyer la colonne 'purchase_date' de manière vectorisée
df_clean = cleaning_date(df_not_clean, 'opened_at')
df_clean.rename(columns = {'opened_at' : 'opened_at_clean'}, inplace = True)

test = pd.concat([df1_campaign_stats[['opened_at']].head(20), df_clean], axis=1)

test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20 entries, 0 to 19
Data columns (total 2 columns):
 #   Column           Non-Null Count  Dtype              
---  ------           --------------  -----              
 0   opened_at        8 non-null      object             
 1   opened_at_clean  8 non-null      datetime64[ns, UTC]
dtypes: datetime64[ns, UTC](1), object(1)
memory usage: 448.0+ bytes


## Nettoyage, selection et fusion

In [23]:
df1_ticket_information

ticket_id  product_id  is_from_subscription  type_of   supplier_name  \
0         13070859      225251                 False        1  vente en ligne   
1         13070860      224914                 False        1  vente en ligne   
2         13070861      224914                 False        1  vente en ligne   
3         13070862      224914                 False        1  vente en ligne   
4         13070863      224914                 False        1  vente en ligne   
...            ...         ...                   ...      ...             ...   
1826667   20662815      405689                 False        1  vente en ligne   
1826668   20662816      403658                 False        1  vente en ligne   
1826669   20662817      403658                 False        1  vente en ligne   
1826670   20662818      403658                 False        1  vente en ligne   
1826671   20662819      403658                 False        1  vente en ligne   

                    purchase_date  customer_id  
0       2018-12-28 14:47:50+00:00        48187  
1       2018-12-28 14:47:50+00:00        48187  
2       2018-12-28 14:47:50+00:00        48187  
3       2018-12-28 14:47:50+00:00        48187  
4       2018-12-28 14:47:50+00:00        48187  
...                           ...          ...  
1826667 2023-11-08 17:23:54+00:00      1256135  
1826668 2023-11-08 18:32:18+00:00      1256136  
1826669 2023-11-08 18:32:18+00:00      1256136  
1826670 2023-11-08 19:30:28+00:00      1256137  
1826671 2023-11-08 19:30:28+00:00      1256137  

[1826672 rows x 7 columns]

In [14]:
df1_ticket_information.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1826672 entries, 0 to 1826671
Data columns (total 7 columns):
 #   Column                Dtype              
---  ------                -----              
 0   ticket_id             int64              
 1   product_id            int64              
 2   is_from_subscription  bool               
 3   type_of               int64              
 4   supplier_name         object             
 5   purchase_date         datetime64[ns, UTC]
 6   customer_id           int64              
dtypes: bool(1), datetime64[ns, UTC](1), int64(4), object(1)
memory usage: 85.4+ MB


# Customer information

## Target area

In [60]:
# Target.csv cleaning
df1_targets_clean = df1_targets[["id", "target_type_id", "name"]]
df1_targets_clean.rename(columns = {'id' : 'target_id' , 'name' : 'target_name'}, inplace = True)

# target_type cleaning
df1_target_types_clean = df1_target_types[["id","is_import","name"]].add_prefix("target_type_")

#customer_target_mappings cleaning
df1_customer_target_mappings_clean = df1_customer_target_mappings[["id", "customer_id", "target_id"]]

# Merge target et target_type
df1_targets_full = pd.merge(df1_targets_clean, df1_target_types_clean, left_on='target_type_id', right_on='target_type_id', how='inner')
df1_targets_full.drop(['target_type_id'], axis = 1, inplace=True)

# Merge
df1_targets_full = pd.merge(df1_customer_target_mappings_clean, df1_targets_full, left_on='target_id', right_on='target_id', how='inner')
df1_targets_full.drop(['target_id'], axis = 1, inplace=True)

/tmp/ipykernel_619/2625134041.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1_targets_clean.rename(columns = {'id' : 'target_id' , 'name' : 'target_name'}, inplace = True)


In [62]:
df1_targets_test = df1_targets_full[['id', 'customer_id']].groupby(['customer_id']).count()
len(df1_targets_test[df1_targets_test['id'] > 1]) / len(df1_targets_test)

# 99,6% des 151 000 client visés sont catégorisés plusieurs fois et en moyenne 5 fois... 
df1_targets_test.mean()


id    5.080902
dtype: float64

In [57]:
df1_targets_full[df1_targets_full['customer_id'] == 1]

id  customer_id                                    target_name  \
8793    4584599            1                consentement optin jeune public   
13249   4567465            1                   DDCP rentrée culturelle 2023   
21424   4544805            1    spectateurs cine dimanche_cine concert_2122   
21665   4544911            1                                 DDCP Cine 2023   
22811   4545766            1                                DDCP OLBJ! 2023   
57305   4457909            1  ddcp_promo_visiteurs occasionnels_musee_8mois   
58843   3688872            1                             DDCP promo livemag   
66813   4313646            1   DDCP spectateurs Classique mais pas que 2022   
68367   4547662            1    ddcp_promo_musee_au moins 3 achats_dps8mois   
77320   4285520            1                      DDCP spectateurs Iminente   
84350   4037805            1       DDCP spectateurs Marseille Jazz 18-19-21   
85383   4569504            1   DDCP rendez-vous de septembre offre spéciale   
92868   4433064            1          ddcp_promo_plein air_ateliers_jardins   
99670   3858684            1                                      Acid Arab   
105477  4321810            1               Arenametrix_bascule tel vers sib   
169513  3697992            1            ddcp_achats billets nb dps 19052021   
214421  2925324            1                  consentement optout scolaires   
234546  4575957            1                       Portrait de Leila shahid   
259808  3722259            1                         consentement optin b2b   
274380  4510423            1                       DDCP_marseille_jazz_2023   
307511  5174466            1                             ddcp actoral 21-22   
357509  4442526            1                           ddcp musique barvalo   
392920  4390642            1     ddcp_md_promo_spectateurs theatre contempo   
449620  4411897            1          FORMATION _ acheteurs optin last year   
503809  4734591            1       consentement optin mediation specialisee   
651222  3554426            1                         consentement optin b2c   
654246  5182212            1    DDCP spectateurs Festival de Marseille 2023   
654395  5182456            1       rencontres_echelle_spectateurs_2021_2023   

        target_type_is_import       target_type_name  
8793                    False   manual_static_filter  
13249                   False   manual_static_filter  
21424                   False   manual_static_filter  
21665                   False   manual_static_filter  
22811                   False   manual_static_filter  
57305                   False  manual_dynamic_filter  
58843                   False   manual_static_filter  
66813                   False   manual_static_filter  
68367                   False  manual_dynamic_filter  
77320                   False   manual_static_filter  
84350                   False   manual_static_filter  
85383                   False   manual_static_filter  
92868                   False   manual_static_filter  
99670                   False   manual_static_filter  
105477                  False   manual_static_filter  
169513                  False   manual_static_filter  
214421                  False   manual_static_filter  
234546                  False   manual_static_filter  
259808                  False   manual_static_filter  
274380                  False   manual_static_filter  
307511                  False   manual_static_filter  
357509                  False   manual_static_filter  
392920                  False   manual_static_filter  
449620                  False  manual_dynamic_filter  
503809                  False   manual_static_filter  
651222                  False   manual_static_filter  
654246                  False   manual_static_filter  
654395                  False   manual_static_filter

## Campaign area

In [52]:
# campaign_stats cleaning 
df1_campaign_stats_clean = df1_campaign_stats[["id", "campaign_id", "customer_id", "opened_at", "sent_at", "delivered_at"]]
cleaning_date(df1_campaign_stats_clean, 'opened_at')
cleaning_date(df1_campaign_stats_clean, 'sent_at')
cleaning_date(df1_campaign_stats_clean, 'delivered_at')

# campaigns cleaning
df1_campaigns_clean = df1_campaigns[["id", "name", "service_id", "sent_at"]].add_prefix("campaign_")
cleaning_date(df1_campaigns_clean, 'campaign_sent_at')

# Merge 
df1_campaigns_full = pd.merge(df1_campaign_stats_clean, df1_campaigns_clean, on = "campaign_id", how = "left")
df1_campaigns_full.drop(['campaign_id'], axis = 1, inplace=True)

/tmp/ipykernel_9792/1967867975.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[column_name] = pd.to_datetime(df[column_name], utc = True, format = 'ISO8601')
/tmp/ipykernel_9792/1967867975.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[column_name] = pd.to_datetime(df[column_name], utc = True, format = 'ISO8601')
/tmp/ipykernel_9792/1967867975.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value in

In [53]:
df1_campaigns_full.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6214808 entries, 0 to 6214807
Data columns (total 8 columns):
 #   Column               Dtype              
---  ------               -----              
 0   id                   int64              
 1   customer_id          int64              
 2   opened_at            datetime64[ns, UTC]
 3   sent_at              datetime64[ns, UTC]
 4   delivered_at         datetime64[ns, UTC]
 5   campaign_name        object             
 6   campaign_service_id  int64              
 7   campaign_sent_at     datetime64[ns, UTC]
dtypes: datetime64[ns, UTC](4), int64(3), object(1)
memory usage: 379.3+ MB


In [56]:
df1_campaigns_information

id  customer_id                 opened_at  \
0          19793       112597                       NaT   
1          14211       113666                       NaT   
2          13150       280561                       NaT   
3           7073       101007 2021-03-28 18:11:06+00:00   
4           5175       103972                       NaT   
...          ...          ...                       ...   
6214803  8302994       266155 2023-10-23 09:43:25+00:00   
6214804  8303307        21355 2023-10-23 09:44:02+00:00   
6214805  8304346        21849 2023-10-23 09:45:52+00:00   
6214806  8302037       667789 2023-10-23 09:47:32+00:00   
6214807  8304939       294154                       NaT   

                          sent_at              delivered_at  \
0       2021-03-28 16:01:09+00:00 2021-03-28 16:24:18+00:00   
1       2021-03-28 16:01:09+00:00 2021-03-28 16:21:02+00:00   
2       2021-03-28 16:00:59+00:00 2021-03-28 16:08:45+00:00   
3       2021-03-28 16:00:59+00:00 2021-03-28 16:09:47+00:00   
4       2021-03-28 16:01:06+00:00 2021-03-28 16:05:03+00:00   
...                           ...                       ...   
6214803 2023-10-23 09:32:33+00:00 2023-10-23 09:32:34+00:00   
6214804 2023-10-23 09:32:49+00:00 2023-10-23 09:32:49+00:00   
6214805 2023-10-23 09:33:28+00:00 2023-10-23 09:33:29+00:00   
6214806 2023-10-23 09:31:53+00:00 2023-10-23 09:31:54+00:00   
6214807 2023-10-23 09:33:54+00:00 2023-10-23 09:33:55+00:00   

                                   campaign_name  campaign_service_id  \
0        Le Mucem chez vous, gardons le lien #22                  404   
1        Le Mucem chez vous, gardons le lien #22                  404   
2        Le Mucem chez vous, gardons le lien #22                  404   
3        Le Mucem chez vous, gardons le lien #22                  404   
4        Le Mucem chez vous, gardons le lien #22                  404   
...                                          ...                  ...   
6214803                             dre_nov_2023                 1318   
6214804                             dre_nov_2023                 1318   
6214805                             dre_nov_2023                 1318   
6214806                             dre_nov_2023                 1318   
6214807                             dre_nov_2023                 1318   

                 campaign_sent_at  
0       2021-03-27 23:00:00+00:00  
1       2021-03-27 23:00:00+00:00  
2       2021-03-27 23:00:00+00:00  
3       2021-03-27 23:00:00+00:00  
4       2021-03-27 23:00:00+00:00  
...                           ...  
6214803 2023-10-23 09:31:17+00:00  
6214804 2023-10-23 09:31:17+00:00  
6214805 2023-10-23 09:31:17+00:00  
6214806 2023-10-23 09:31:17+00:00  
6214807 2023-10-23 09:31:17+00:00  

[6214808 rows x 8 columns]

## Link area

In [37]:
df1_campaigns

id                                               name  service_id  \
0    1319613                newsletter enseignants janvier 2022         721   
1    1319586                                   lsf_janvier_2022         717   
2    1319282  Invitation à déjeuner au Mucem | Vernissage « ...         591   
3    1319283     Vacances de la Toussaint - centres des loisirs         590   
4    1319636                              ddcp_promo_md_livemag         730   
..       ...                                                ...         ...   
952  1320072                                       dre_gaza0106         881   
953   661398          DDCP Plan Bis 4 - Marketing direct - MJ5C         183   
954  1320487                 Invitation portes ouvertes amitiés         988   
955   906903  DDCP PROMO La méditerranée des philosophes #3 ...         310   
956   579313             ddcp_promo_automation_manuel_pre_visit         481   

                           created_at                        updated_at  \
0    2022-01-14 16:06:42.586321+01:00  2022-02-03 14:17:27.112963+01:00   
1    2022-01-07 11:30:35.315895+01:00  2022-02-03 14:17:27.116171+01:00   
2    2021-09-28 12:50:24.448752+02:00  2022-02-03 14:17:27.119582+01:00   
3    2021-09-28 18:01:04.692073+02:00  2022-02-03 14:17:27.124408+01:00   
4    2022-01-27 18:00:41.053069+01:00  2022-02-03 14:17:27.127607+01:00   
..                                ...                               ...   
952  2022-05-26 09:01:35.523639+02:00  2022-12-02 17:51:22.614046+01:00   
953  2021-06-18 10:30:01.259578+02:00  2021-09-24 11:56:09.082785+02:00   
954  2022-09-29 18:01:33.834090+02:00  2022-12-02 17:51:23.258324+01:00   
955  2021-07-19 14:07:16.177390+02:00  2021-09-24 11:56:09.086101+02:00   
956  2021-06-08 17:38:54.041310+02:00  2021-09-24 11:56:09.089394+02:00   

     process_id  report_url  category  to_be_synced  \
0           NaN         NaN       0.0         False   
1           NaN         NaN       0.0         False   
2           NaN         NaN       0.0         False   
3           NaN         NaN       0.0         False   
4           NaN         NaN       0.0         False   
..          ...         ...       ...           ...   
952         NaN         NaN       0.0         False   
953         NaN         NaN       0.0         False   
954         NaN         NaN       0.0         False   
955         NaN         NaN       0.0         False   
956         NaN         NaN       0.0         False   

                           identifier                    sent_at  
0    aba3b6fd5d186d28e06ff97135cade7f  2022-01-14 00:00:00+01:00  
1    788d986905533aba051261497ecffcbb  2022-01-07 00:00:00+01:00  
2    3493894fa4ea036cfc6433c3e2ee63b0  2021-09-28 00:00:00+02:00  
3    08b255a5d42b89b0585260b6f2360bdd  2021-09-28 00:00:00+02:00  
4    d5cfead94f5350c12c322b5b664544c1  2022-01-27 00:00:00+01:00  
..                                ...                        ...  
952  7504adad8bb96320eb3afdd4df6e1f60  2022-05-26 00:00:00+02:00  
953  cedebb6e872f539bef8c3f919874e9d7  2020-07-27 00:00:00+02:00  
954  9908279ebbf1f9b250ba689db6a0222b  2022-09-29 00:00:00+02:00  
955  06eb61b839a0cefee4967c67ccb099dc  2020-12-23 00:00:00+01:00  
956  9461cce28ebe3e76fb4b931c35a169b0  2021-06-08 00:00:00+02:00  

[957 rows x 11 columns]

In [38]:
df1_link_stats

id                 clicked_at  link_id  customer_id  \
0            1  2021-03-26 16:30:36+01:00        1       284033   
1            2  2021-03-26 17:16:34+01:00        2       119768   
2          272  2021-03-28 20:03:32+02:00       42       113105   
3            4  2021-03-26 17:43:19+01:00        3       272280   
4            5  2021-03-26 17:46:00+01:00        3       105095   
...        ...                        ...      ...          ...   
151046  243553  2023-11-09 16:34:27+01:00    14666          998   
151047  243554  2023-11-09 16:34:35+01:00    14670          998   
151048  243559  2023-11-09 16:51:15+01:00    14686        82923   
151049  243561  2023-11-09 16:59:42+01:00    14677        82923   
151050  243564  2023-11-09 17:16:41+01:00    14691      1254355   

                              created_at                        updated_at  
0       2021-03-26 15:30:37.050161+01:00  2021-03-26 15:30:37.050161+01:00  
1       2021-03-26 16:16:34.950871+01:00  2021-03-26 16:16:34.950871+01:00  
2       2021-03-28 18:03:32.736394+02:00  2021-03-28 18:03:32.736394+02:00  
3       2021-03-26 16:43:19.338321+01:00  2021-03-26 16:43:19.338321+01:00  
4       2021-03-26 16:46:00.502945+01:00  2021-03-26 16:46:00.502945+01:00  
...                                  ...                               ...  
151046  2023-11-09 15:34:29.425425+01:00  2023-11-09 15:34:29.425425+01:00  
151047  2023-11-09 15:34:37.505505+01:00  2023-11-09 15:34:37.505505+01:00  
151048  2023-11-09 15:51:17.439518+01:00  2023-11-09 15:51:17.439518+01:00  
151049  2023-11-09 15:59:44.030922+01:00  2023-11-09 15:59:44.030922+01:00  
151050  2023-11-09 16:16:43.012932+01:00  2023-11-09 16:16:43.012932+01:00  

[151051 rows x 6 columns]

## Exploration variables

In [7]:
# Fonction d'exploration pour suppliers.csv = label itr et commission inconnues
def suppliers_exploration(suppliers = None) : 
    
    # Taux de NaN pour ces colonnes
    label_na = suppliers['label'].isna().sum()/len(suppliers)*100
    itr_na = suppliers['itr'].isna().sum()/len(suppliers)*100
    commission_na = suppliers['commission'].isna().sum()/len(suppliers)*100

    suppliers_desc = pd.DataFrame({'nb_suppliers' : [suppliers['name'].nunique()],
                                  'label_na' : [label_na],
                                  'itr_na' : [itr_na],
                                  'commission_na' : [commission_na]})

    return suppliers_desc

In [8]:
df1_suppliers_desc = suppliers_exploration(suppliers = df1_suppliers)

In [9]:
df1_suppliers_desc

nb_suppliers  label_na  itr_na  commission_na
0             9     100.0   100.0          100.0

In [10]:
BUCKET = "bdc2324-data"
liste_folders = fs.ls(BUCKET)

liste_files = []
for company_folder in liste_folders : 
    liste_files.extend(fs.ls(company_folder))

In [11]:
liste_database_select = ['suppliers']

# Filtrer la liste pour les éléments contenant au moins un élément de la liste à tester
liste_suppliers = [element for element in liste_files if any(element_part in element for element_part in liste_database_select)]

# Afficher le résultat
print(liste_suppliers)

['bdc2324-data/1/1suppliers.csv', 'bdc2324-data/10/10suppliers.csv', 'bdc2324-data/101/101suppliers.csv', 'bdc2324-data/11/11suppliers.csv', 'bdc2324-data/12/12suppliers.csv', 'bdc2324-data/13/13suppliers.csv', 'bdc2324-data/14/14suppliers.csv', 'bdc2324-data/2/2suppliers.csv', 'bdc2324-data/3/3suppliers.csv', 'bdc2324-data/4/4suppliers.csv', 'bdc2324-data/5/5suppliers.csv', 'bdc2324-data/6/6suppliers.csv', 'bdc2324-data/7/7suppliers.csv', 'bdc2324-data/8/8suppliers.csv', 'bdc2324-data/9/9suppliers.csv']


In [32]:
# loop to create dataframes from file 2
def database_loading(database_name = None):
    files_path = database_name
    
    client_number = files_path.split("/")[1]
    df_prefix = "df" + str(client_number) + "_"
    
    current_path = files_path
    with fs.open(current_path, mode="rb") as file_in:
        df = pd.read_csv(file_in)

    return df, client_number

In [45]:
df_all = pd.DataFrame()

for link in liste_suppliers:
    
    df_supplier, tenant_id = database_loading(link)
    
    df_supplier['tenant_id'] = int(tenant_id)

    df_all = pd.concat([df_all, df_supplier], axis = 0)
    

In [63]:
# df_all[df_all['tenant_id'] == 101]['name'].unique()

In [66]:
liste_mots = ['en ligne', 'internet', 'web', 'net', 'vad', 'online'] 
# vad = vente à distance
df_all['name'] = df_all['name'].fillna('')

df_all['canal_vente_internet'] = df_all['name'].str.contains('|'.join(liste_mots), case=False).astype(int)


In [68]:
df_all.groupby('tenant_id')['canal_vente_internet'].max()

tenant_id
1      1
2      1
3      1
4      1
5      1
6      1
7      1
8      1
9      1
10     1
11     1
12     1
13     1
14     1
101    1
Name: canal_vente_internet, dtype: int64